In [58]:
# %%
from calo_cluster.datasets.hcal_tt import HCalTTOffsetDataModule
from pathlib import Path
import plotly.express as px
import pandas as pd
from tqdm.auto import tqdm
import numpy as np
from calo_cluster.evaluation.utils import get_palette
from functools import partial
import multiprocessing as mp

In [51]:
root = Path('/global/cscratch1/sd/schuya/calo_cluster/data/hgcal/npzs_all')
out_dir = Path('/global/cscratch1/sd/schuya/calo_cluster/data/hgcal/raw')

In [60]:
files = [f for f in root.glob('*.npz')]

In [5]:
evt = np.load(files[0])

In [62]:
len(files)

19890

In [10]:
[f for f in evt.keys()]

['recHitFeatures',
 'recHitFeatures_rowsplits',
 'recHitTruthClusterIdx',
 'recHitTruthClusterIdx_rowsplits',
 'recHitTruthEnergy',
 'recHitTruthEnergy_rowsplits',
 'recHitTruthPosition',
 'recHitTruthPosition_rowsplits',
 'recHitTruthTime',
 'recHitTruthTime_rowsplits',
 'recHitTruthID',
 'recHitTruthID_rowsplits',
 'recHitSpectatorFlag',
 'recHitSpectatorFlag_rowsplits',
 'recHitFullyContainedFlag',
 'recHitFullyContainedFlag_rowsplits']

In [52]:
def to_pickle(f, out_dir):
    evt = np.load(f)
    d = {}
    for i, name in enumerate(['energy', 'eta', 'zero', 'theta', 'r', 'x', 'y', 'z', 'time']):
        if name != 'zero':
            d[name] = evt['recHitFeatures'][:, i]
    df = pd.DataFrame(d)
    df['cluster_id'] = evt['recHitTruthClusterIdx'][:,0]
    df['hit'] = (df['cluster_id'] != -1).astype(int)
    df.to_pickle(out_dir / f'{f.stem}.pkl')

In [63]:
with mp.Pool(10) as p:
    with tqdm(total=len(files)) as pbar:
        for _ in p.imap_unordered(partial(to_pickle, out_dir=out_dir), files):
            pbar.update()

  0%|          | 0/19890 [00:00<?, ?it/s]

In [54]:
df = pd.read_pickle(out_dir / '38_nanoML_53.pkl')

In [55]:
df['hit'] = df['hit'].astype(str)
df['cluster_id'] = df['cluster_id'].astype(str)

In [56]:
px.scatter_3d(df, x='x', y='y', z='z', size='energy', color='hit')

In [57]:
px.scatter_3d(df, x='x', y='y', z='z', size='energy', color='cluster_id', color_discrete_sequence=get_palette(df['cluster_id']))

In [65]:
from calo_cluster.datasets.hgcal_taus import HGCalTausOffsetDataModule

In [67]:
dm = HGCalTausOffsetDataModule.from_config(['dataset.event_size=0.1'])

Global seed set to 1588147245


In [68]:

dm.voxel_occupancy()

  0%|          | 0/15912 [00:00<?, ?it/s]

KeyboardInterrupt: 